### Convert shapefiles from zillow data into geojason for follium.

Zillow data is available [here](https://www.zillow.com/howto/api/neighborhood-boundaries.htm)

```bash
%%bash
cd zillowdata
for d in $(find . -maxdepth 1 -type d -not -path ".")
do
  for f in $(find $d -name "*.shp")
  do
   ogr2ogr -f GeoJSON -t_srs EPSG:4326 -simplify 1000 "$(echo $d | cut -c3-).geojson" $f
  done
  
done
```

In [1]:
import folium
import os
import json
from shapely.geometry import Polygon
import math
from folium.plugins import MarkerCluster
import pandas as pd

labels = [
    'Name',
    'Location',
    'Size'
]
zpath = "./zillowdata/"
neighborhoods = pd.DataFrame(columns=labels)
for filename in [f for f in os.listdir(zpath) if "geojson" in f]:
    with open(zpath + filename) as f:
        data = json.load(f)
        for neighborhood in data["features"]:
#             Neighborhoods with multiple shapes defining their borders are ignored
            if neighborhood["geometry"]["type"] == "MultiPolygon":
                continue
            name = neighborhood["properties"]["Name"].replace("'", "\'")
#             Some neighborhoods with poorly formatted coordinates are ignored
            coords = neighborhood["geometry"]["coordinates"]
            while coords[0][0][0] == list:
                coords = coords[0]
            if len(coords) > 1:
                continue
            coords = coords[0]
#             A polygon is constructed to calculate the size of the neighborhood
            polygon = Polygon(coords)
            area = polygon.area
            xs = [point[0] for point in coords]
            ys = [point[1] for point in coords]
            center = ((sum(ys[1:]))/(len(ys)-1), (sum(xs[1:]))/(len(xs)-1))
            neighborhoods.loc[len(neighborhoods)] = [name, center, area * 100000]
            
neighborhoods.head()

Name                                   Location        Size
0          West Valley   (43.63821095330781, -116.31124328349995)  130.632496
1        West Downtown  (43.617511426057845, -116.21884201299994)   29.782147
2      West Cloverdale  (43.638623543307816, -116.33952629899993)   10.345858
3  South Boise Village   (43.59153704305788, -116.20124626249992)    8.317578
4          Quail Ridge   (43.66947425805778, -116.23805885399996)   12.439082

In [2]:
neighborhoods.describe()

Size
count  16366.000000
mean      26.015394
std       84.490901
min        0.000080
25%        3.766563
50%        9.423381
75%       22.869927
max     4059.465044

In [3]:
#### Build map with circles
import json
from shapely.geometry import Polygon
import math
from folium.plugins import MarkerCluster

def map_circles(df):
    m = folium.Map(
        location=[36.64699473120942, -75.99394080442949],
        zoom_start=4.3
    )
    for _, nh in df.iterrows():
        folium.Circle(
            radius=250 * math.sqrt(nh["Size"]/math.pi),
            location=nh["Location"],
            popup=nh["Name"].replace("'", ""),
            clustered_marker = True,
            color='#3186cc',
            fill=True,
            fill_color='#3186cc'
        ).add_to(m)
    m.save("map.html")
    print("Saved map")
    return m

In [4]:
map_circles(neighborhoods)
"Done"

Saved map


'Done'

In [5]:
from dotenv import load_dotenv
import os

load_dotenv(dotenv_path='./foursquare.env')

CLIENT_ID = os.getenv('FS_ID') # your Foursquare ID
CLIENT_SECRET = os.getenv('FS_SECRET') # your Foursquare Secret
VERSION = '20180605' # Foursquare API version

In [6]:
# function that extracts the category of the venue
def get_category_type(row):
    try:
        categories_list = row['categories']
    except:
        categories_list = row['venue.categories']
        
    if len(categories_list) == 0:
        return None
    else:
        return categories_list[0]['name']

In [7]:
import requests

def getNearbyVenues(df, limit=250):
    
    venues_list=[]
    i = df.shape[0]
    for _, (Name, Location, Size) in df.iterrows():
        lat = Location[0]
        lng = Location[1]
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            Size * 10, 
            limit)
            
        # make the GET request
        print("Getting venues for", Name, i)
        i = i - 1
        try:
            response = requests.get(url).json()
            results = response["response"]['groups'][0]['items']
        except KeyError:
            print(response)
            continue
#         print("results: ", results)
        # return only relevant information for each nearby venue
        venues_list.append([(
            Name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])
    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Neighborhood', 
                  'Neighborhood Latitude', 
                  'Neighborhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']

    return(nearby_venues)

In [8]:
df = neighborhoods[0:20]
venues = getNearbyVenues(df)
m = folium.Map(
    location=[36.64699473120942, -75.99394080442949],
    zoom_start=4.3
)
for _, nh in venues.iterrows():
    folium.Marker(
        location=(nh["Venue Latitude"], nh["Venue Longitude"]),
        popup=nh["Neighborhood"].replace("'", ""),
    ).add_to(m)

for _, nh in df.iterrows():
    folium.Circle(
        radius=250 * math.sqrt(nh["Size"]/math.pi),
        location=nh["Location"],
        popup=nh["Name"].replace("'", ""),
        clustered_marker = True,
        color='#3186cc',
        fill=True,
        fill_color='#3186cc'
    ).add_to(m)
m.save("map.html")
print("Saved map")
m

Getting venues for West Valley 20
Getting venues for West Downtown 19
Getting venues for West Cloverdale 18
Getting venues for South Boise Village 17
Getting venues for Quail Ridge 16
Getting venues for East End 15
Getting venues for Downtown 14
Getting venues for Glenwood Rim 13
{'meta': {'code': 500, 'errorType': 'server_error', 'errorDetail': 'Foursquare servers are experiencing problems. Please retry and check status.foursquare.com for updates.'}, 'response': {}}
Getting venues for Central Bench 12
Getting venues for Harris Ranch 11
Getting venues for North End 10
Getting venues for Southeast Boise 9
Getting venues for West Bench 8
Getting venues for Boise Airport 7
Getting venues for Warm Springs Mesa 6
Getting venues for Winstead Park 5
Getting venues for Hillcrest 4
Getting venues for Highlands 3
Getting venues for Vista 2
Getting venues for Borah 1
Saved map


In [9]:
import os

if(not os.path.isfile("./venues.csv")):
    venues = getNearbyVenues(neighborhoods)
    venues.to_csv("./venues.csv")
else:
    venues = pd.read_csv("./venues.csv")
venues.head()

Unnamed: 0 Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0           0  West Valley              43.638211             -116.311243   
1           1  West Valley              43.638211             -116.311243   
2           2  West Valley              43.638211             -116.311243   
3           3  West Valley              43.638211             -116.311243   
4           4  West Valley              43.638211             -116.311243   

             Venue  Venue Latitude  Venue Longitude        Venue Category  
0   Fiesta Chicken       43.633479      -116.315480    Mexican Restaurant  
1       Albertsons       43.634666      -116.316204         Grocery Store  
2   SONIC Drive In       43.634453      -116.312822  Fast Food Restaurant  
3        Starbucks       43.634488      -116.315901           Coffee Shop  
4  Weight Watchers       43.635040      -116.315507    Weight Loss Center

In [10]:
venues[venues["Venue Category"] == "College Tennis Court"]

Unnamed: 0                     Neighborhood  Neighborhood Latitude  \
31415       31415  East Memphis-Colonial-Yorkshire              35.116007   

       Neighborhood Longitude             Venue  Venue Latitude  \
31415              -89.930765  The Racquet Club       35.116183   

       Venue Longitude        Venue Category  
31415        -89.89023  College Tennis Court

In [11]:
print('There are {} uniques categories.'.format(len(venues['Venue Category'].unique())))

There are 596 uniques categories.


In [12]:
# one hot encoding
onehot = pd.get_dummies(venues[['Venue Category']], prefix="", prefix_sep="")
onehot['Neighborhood'] = venues['Neighborhood']
onehot['Neighborhood Latitude'] = venues['Neighborhood Latitude']
onehot['Neighborhood Longitude'] = venues['Neighborhood Longitude']
onehot['Total'] = onehot.drop(columns=["Neighborhood Latitude", "Neighborhood Longitude"]).sum(axis=1)
onehot.drop(onehot[onehot["Total"] < 1].index, inplace=True)
onehot.drop("Total", axis=1, inplace=True)
onehot.set_index(["Neighborhood", "Neighborhood Latitude", "Neighborhood Longitude"], inplace=True)
onehot.loc['East Memphis-Colonial-Yorkshire']
onehot.head()

ATM  \
Neighborhood Neighborhood Latitude Neighborhood Longitude        
West Valley  43.638211             -116.311243               0   
                                   -116.311243               0   
                                   -116.311243               0   
                                   -116.311243               0   
                                   -116.311243               0   

                                                           Accessories Store  \
Neighborhood Neighborhood Latitude Neighborhood Longitude                      
West Valley  43.638211             -116.311243                             0   
                                   -116.311243                             0   
                                   -116.311243                             0   
                                   -116.311243                             0   
                                   -116.311243                             0   

                                                           Adult Boutique  \
Neighborhood Neighborhood Latitude Neighborhood Longitude                   
West Valley  43.638211             -116.311243                          0   
                                   -116.311243                          0   
                                   -116.311243                          0   
                                   -116.311243                          0   
                                   -116.311243                          0   

                                                           Advertising Agency  \
Neighborhood Neighborhood Latitude Neighborhood Longitude                       
West Valley  43.638211             -116.311243                              0   
                                   -116.311243                              0   
                                   -116.311243                              0   
                                   -116.311243                              0   
                                   -116.311243                              0   

                                                           Afghan Restaurant  \
Neighborhood Neighborhood Latitude Neighborhood Longitude                      
West Valley  43.638211             -116.311243                             0   
                                   -116.311243                             0   
                                   -116.311243                             0   
                                   -116.311243                             0   
                                   -116.311243                             0   

                                                           African Restaurant  \
Neighborhood Neighborhood Latitude Neighborhood Longitude                       
West Valley  43.638211             -116.311243                              0   
                                   -116.311243                              0   
                                   -116.311243                              0   
                                   -116.311243                              0   
                                   -116.311243                              0   

                                                           Airport  \
Neighborhood Neighborhood Latitude Neighborhood Longitude            
West Valley  43.638211             -116.311243                   0   
                                   -116.311243                   0   
                                   -116.311243                   0   
                                   -116.311243                   0   
                                   -116.311243                   0   

                                                           Airport Food Court  \
Neighborhood Neighborhood Latitude Neighborhood Longitude                       
West Valley  43.638211             -116.311243                              0   
                                   -116.311243                  

In [13]:
onehot["College Tennis Court"].describe()

count    51399.000000
mean         0.000019
std          0.004411
min          0.000000
25%          0.000000
50%          0.000000
75%          0.000000
max          1.000000
Name: College Tennis Court, dtype: float64

In [14]:
grouped = onehot.groupby(['Neighborhood', 'Neighborhood Latitude', 'Neighborhood Longitude']).mean()
grouped.head()

ATM  \
Neighborhood        Neighborhood Latitude Neighborhood Longitude        
19th Ward           43.143592             -77.648521              0.0   
29 North            38.062210             -78.487690              0.0   
33rd St. Industrial 28.504929             -81.435576              0.0   
39th East           39.044526             -94.375892              0.0   
65th St. West       34.679176             -92.377483              0.0   

                                                                  Accessories Store  \
Neighborhood        Neighborhood Latitude Neighborhood Longitude                      
19th Ward           43.143592             -77.648521                            0.0   
29 North            38.062210             -78.487690                            0.0   
33rd St. Industrial 28.504929             -81.435576                            0.0   
39th East           39.044526             -94.375892                            0.0   
65th St. West       34.679176             -92.377483                            0.0   

                                                                  Adult Boutique  \
Neighborhood        Neighborhood Latitude Neighborhood Longitude                   
19th Ward           43.143592             -77.648521                         0.0   
29 North            38.062210             -78.487690                         0.0   
33rd St. Industrial 28.504929             -81.435576                         0.0   
39th East           39.044526             -94.375892                         0.0   
65th St. West       34.679176             -92.377483                         0.0   

                                                                  Advertising Agency  \
Neighborhood        Neighborhood Latitude Neighborhood Longitude                       
19th Ward           43.143592             -77.648521                             0.0   
29 North            38.062210             -78.487690                             0.0   
33rd St. Industrial 28.504929             -81.435576                             0.0   
39th East           39.044526             -94.375892                             0.0   
65th St. West       34.679176             -92.377483                             0.0   

                                                                  Afghan Restaurant  \
Neighborhood        Neighborhood Latitude Neighborhood Longitude                      
19th Ward           43.143592             -77.648521                            0.0   
29 North            38.062210             -78.487690                            0.0   
33rd St. Industrial 28.504929             -81.435576                            0.0   
39th East           39.044526             -94.375892                            0.0   
65th St. West       34.679176             -92.377483                            0.0   

                                                                  African Restaurant  \
Neighborhood        Neighborhood Latitude Neighborhood Longitude                       
19th Ward           43.143592             -77.648521                             0.0   
29 North            38.062210             -78.487690                             0.0   
33rd St. Industrial 28.504929             -81.435576                             0.0   
39th East           39.044526             -94.375892                             0.0   
65th St. West       34.679176             -92.377483                             0.0   

                                                                  Airport  \
Neighborhood        Neighborhood Latitude Neighborhood Longitude            
19th Ward           43.143592             -77.648521                  0.0   
29 North            38.062210             -78.487690                  0.0   
33rd St. Industrial 28.504929             -81.435576                  0.0   
39th East           39.044526             -94.375892                  0.0   
65th St. West       34.679176             -92.377

In [15]:
# A lot of neighborhoods don't have any venues. 
# I suspect they're either residential, or in areas that don't have high foursquare use.
neighborhoods.loc[~neighborhoods.index.isin(grouped.index.get_level_values('Neighborhood'))].shape

(16366, 3)

In [16]:
num_top_venues = 5
num_hoods = 25

for hood in grouped.index.get_level_values('Neighborhood')[:num_hoods]:
    print("----"+hood+"----")
    temp = grouped.loc[hood].T.reset_index()
    temp.columns = ['venue','freq']
    temp = temp.iloc[1:]
    temp['freq'] = temp['freq'].astype(float)
    temp = temp.round({'freq': 2})
    print(temp.sort_values('freq', ascending=False).reset_index(drop=True).head(num_top_venues))
    print('\n')

----19th Ward----
                  venue  freq
0  Caribbean Restaurant  0.17
1                  Park  0.17
2                Market  0.17
3         Grocery Store  0.17
4           Pizza Place  0.17


----29 North----
                           venue  freq
0                          Hotel   1.0
1              Accessories Store   0.0
2           Pakistani Restaurant   0.0
3                         Palace   0.0
4  Paper / Office Supplies Store   0.0


----33rd St. Industrial----
                  venue  freq
0                Office   1.0
1     Accessories Store   0.0
2      Pedestrian Plaza   0.0
3  Pakistani Restaurant   0.0
4                Palace   0.0


----39th East----
                           venue  freq
0                      Bookstore  0.50
1                    Fabric Shop  0.25
2                  Shopping Mall  0.25
3              Accessories Store  0.00
4  Paper / Office Supplies Store  0.00


----65th St. West----
                        venue  freq
0  Financial or Legal Ser

In [17]:
# Let's use mean normalization to preprocess the data.
grouped.describe()

ATM  Accessories Store  Adult Boutique  Advertising Agency  \
count  5182.000000        5182.000000     5182.000000         5182.000000   
mean      0.000944           0.000930        0.000012            0.000271   
std       0.012007           0.021804        0.000480            0.014380   
min       0.000000           0.000000        0.000000            0.000000   
25%       0.000000           0.000000        0.000000            0.000000   
50%       0.000000           0.000000        0.000000            0.000000   
75%       0.000000           0.000000        0.000000            0.000000   
max       0.500000           1.000000        0.022222            1.000000   

       Afghan Restaurant  African Restaurant      Airport  Airport Food Court  \
count        5182.000000         5182.000000  5182.000000         5182.000000   
mean            0.000025            0.000208     0.001430            0.000075   
std             0.001175            0.007804     0.022108            0.003219   
min             0.000000            0.000000     0.000000            0.000000   
25%             0.000000            0.000000     0.000000            0.000000   
50%             0.000000            0.000000     0.000000            0.000000   
75%             0.000000            0.000000     0.000000            0.000000   
max             0.076923            0.500000     1.000000            0.200000   

       Airport Lounge  Airport Service     ...        Whisky Bar     Wine Bar  \
count     5182.000000      5182.000000     ...       5182.000000  5182.000000   
mean         0.000153         0.000704     ...          0.000180     0.002814   
std          0.004048         0.014286     ...          0.005392     0.036438   
min          0.000000         0.000000     ...          0.000000     0.000000   
25%          0.000000         0.000000     ...          0.000000     0.000000   
50%          0.000000         0.000000     ...          0.000000     0.000000   
75%          0.000000         0.000000     ...          0.000000     0.000000   
max          0.200000         0.500000     ...          0.333333     1.000000   

         Wine Shop       Winery  Wings Joint  Women's Store  \
count  5182.000000  5182.000000  5182.000000    5182.000000   
mean      0.001044     0.000168     0.001707       0.001195   
std       0.018525     0.005136     0.021059       0.019349   
min       0.000000     0.000000     0.000000       0.000000   
25%       0.000000     0.000000     0.000000       0.000000   
50%       0.000000     0.000000     0.000000       0.000000   
75%       0.000000     0.000000     0.000000       0.000000   
max       1.000000     0.250000     1.000000       1.000000   

       Xinjiang Restaurant  Yoga Studio          Zoo  Zoo Exhibit  
count          5182.000000  5182.000000  5182.000000  5182.000000  
mean              0.000021     0.002863     0.000340     0.001212  
std               0.001396     0.038827     0.008417     0.027804  
min               0.000000     0.000000     0.000000     0.000000  
25%               0.000000     0.000000     0.000000     0.000000  
50%               0.000000     0.000000     0.000000     0.000000  
75%               0.000000     0.000000     0.000000     0.000000  
max               0.100000     1.000000     0.333333     1.000000  

[8 rows x 595 columns]

In [18]:
normal_data = (grouped - grouped.mean())/grouped.std()
normal_data.round(3).describe()

ATM  Accessories Store  Adult Boutique  Advertising Agency  \
count  5182.000000        5182.000000     5182.000000         5182.000000   
mean     -0.000355          -0.000355       -0.000019           -0.000159   
std       1.000028           1.000007        1.000004            1.000006   
min      -0.079000          -0.043000       -0.024000           -0.019000   
25%      -0.079000          -0.043000       -0.024000           -0.019000   
50%      -0.079000          -0.043000       -0.024000           -0.019000   
75%      -0.079000          -0.043000       -0.024000           -0.019000   
max      41.564000          45.821000       46.304000           69.523000   

       Afghan Restaurant  African Restaurant      Airport  Airport Food Court  \
count        5182.000000         5182.000000  5182.000000         5182.000000   
mean            0.000214           -0.000337    -0.000321            0.000267   
std             0.999995            1.000016     1.000024            1.000000   
min            -0.021000           -0.027000    -0.065000           -0.023000   
25%            -0.021000           -0.027000    -0.065000           -0.023000   
50%            -0.021000           -0.027000    -0.065000           -0.023000   
75%            -0.021000           -0.027000    -0.065000           -0.023000   
max            65.438000           64.043000    45.167000           62.102000   

       Airport Lounge  Airport Service     ...        Whisky Bar     Wine Bar  \
count     5182.000000      5182.000000     ...       5182.000000  5182.000000   
mean        -0.000129         0.000251     ...          0.000442     0.000229   
std          0.999998         0.999993     ...          0.999981     0.999984   
min         -0.038000        -0.049000     ...         -0.033000    -0.077000   
25%         -0.038000        -0.049000     ...         -0.033000    -0.077000   
50%         -0.038000        -0.049000     ...         -0.033000    -0.077000   
75%         -0.038000        -0.049000     ...         -0.033000    -0.077000   
max         49.363000        34.949000     ...         61.788000    27.366000   

         Wine Shop       Winery  Wings Joint  Women's Store  \
count  5182.000000  5182.000000  5182.000000    5182.000000   
mean      0.000355    -0.000322     0.000059      -0.000215   
std       0.999979     1.000004     0.999991       1.000012   
min      -0.056000    -0.033000    -0.081000      -0.062000   
25%      -0.056000    -0.033000    -0.081000      -0.062000   
50%      -0.056000    -0.033000    -0.081000      -0.062000   
75%      -0.056000    -0.033000    -0.081000      -0.062000   
max      53.925000    48.642000    47.404000      51.619000   

       Xinjiang Restaurant  Yoga Studio          Zoo  Zoo Exhibit  
count          5182.000000  5182.000000  5182.000000  5182.000000  
mean              0.000205    -0.000260     0.000450    -0.000409  
std               0.999997     1.000022     0.999991     1.000019  
min              -0.015000    -0.074000    -0.040000    -0.044000  
25%              -0.015000    -0.074000    -0.040000    -0.044000  
50%              -0.015000    -0.074000    -0.040000    -0.044000  
75%              -0.015000    -0.074000    -0.040000    -0.044000  
max              71.615000    25.682000    39.564000    35.923000  

[8 rows x 595 columns]

In [19]:
print(normal_data.shape)
s = normal_data.isnull().sum()
s[s != 0]

(5182, 595)


Series([], dtype: int64)

In [20]:
from sklearn.cluster import KMeans

# set number of clusters
kclusters = 5

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(normal_data)

# check cluster labels generated for each row in the dataframe
kmeans.labels_.shape

(5182,)

In [21]:
merged = normal_data

# add clustering labels
merged['Cluster Label'] = kmeans.labels_


merged[merged["Cluster Label"] == 0].round(2).describe()

ATM  Accessories Store  Adult Boutique  Advertising Agency  \
count  1860.000000        1860.000000     1860.000000         1860.000000   
mean      0.133527           0.006618        0.046801           -0.014237   
std       1.655805           0.424442        1.668306            0.154790   
min      -0.080000          -0.040000       -0.020000           -0.020000   
25%      -0.080000          -0.040000       -0.020000           -0.020000   
50%      -0.080000          -0.040000       -0.020000           -0.020000   
75%      -0.080000          -0.040000       -0.020000           -0.020000   
max      41.560000          11.420000       46.300000            4.950000   

       Afghan Restaurant  African Restaurant      Airport  Airport Food Court  \
count        1860.000000         1860.000000  1860.000000         1860.000000   
mean            0.039102           -0.013113    -0.007172            0.026258   
std             1.668758            0.300031     0.668516            1.464644   
min            -0.020000           -0.030000    -0.060000           -0.020000   
25%            -0.020000           -0.030000    -0.060000           -0.020000   
50%            -0.020000           -0.030000    -0.060000           -0.020000   
75%            -0.020000           -0.030000    -0.060000           -0.020000   
max            65.440000            8.520000    22.550000           62.100000   

       Airport Lounge  Airport Service      ...           Wine Bar  \
count     1860.000000      1860.000000      ...        1860.000000   
mean         0.042457        -0.018430      ...          -0.026161   
std          1.500276         0.393045      ...           0.387318   
min         -0.040000        -0.050000      ...          -0.080000   
25%         -0.040000        -0.050000      ...          -0.080000   
50%         -0.040000        -0.050000      ...          -0.080000   
75%         -0.040000        -0.050000      ...          -0.080000   
max         49.360000         7.320000      ...           6.780000   

         Wine Shop       Winery  Wings Joint  Women's Store  \
count  1860.000000  1860.000000  1860.000000    1860.000000   
mean      0.014473    -0.017301     0.096446       0.106602   
std       0.547180     0.351714     1.483314       1.659572   
min      -0.060000    -0.030000    -0.080000      -0.060000   
25%      -0.060000    -0.030000    -0.080000      -0.060000   
50%      -0.060000    -0.030000    -0.080000      -0.060000   
75%      -0.060000    -0.030000    -0.080000      -0.060000   
max      10.740000    13.870000    47.400000      51.620000   

       Xinjiang Restaurant  Yoga Studio          Zoo  Zoo Exhibit  \
count          1860.000000  1860.000000  1860.000000  1860.000000   
mean              0.022371    -0.009210    -0.020935    -0.033844   
std               1.669322     0.453882     0.396646     0.152543   
min              -0.020000    -0.070000    -0.040000    -0.040000   
25%              -0.020000    -0.070000    -0.040000    -0.040000   
50%              -0.020000    -0.070000    -0.040000    -0.040000   
75%              -0.020000    -0.070000    -0.040000    -0.040000   
max              71.620000    12.800000    11.840000     5.090000   

       Cluster Label  
count         1860.0  
mean             0.0  
std              0.0  
min              0.0  
25%              0.0  
50%              0.0  
75%              0.0  
max              0.0  

[8 rows x 596 columns]

In [22]:
merged[merged["Cluster Label"] == 1].round(2).describe()

ATM  Accessories Store  Adult Boutique  Advertising Agency  \
count  6.00               6.00            6.00                6.00   
mean  -0.08              -0.04           -0.02               -0.02   
std    0.00               0.00            0.00                0.00   
min   -0.08              -0.04           -0.02               -0.02   
25%   -0.08              -0.04           -0.02               -0.02   
50%   -0.08              -0.04           -0.02               -0.02   
75%   -0.08              -0.04           -0.02               -0.02   
max   -0.08              -0.04           -0.02               -0.02   

       Afghan Restaurant  African Restaurant  Airport  Airport Food Court  \
count               6.00                6.00     6.00                6.00   
mean               -0.02               -0.03    -0.06               -0.02   
std                 0.00                0.00     0.00                0.00   
min                -0.02               -0.03    -0.06               -0.02   
25%                -0.02               -0.03    -0.06               -0.02   
50%                -0.02               -0.03    -0.06               -0.02   
75%                -0.02               -0.03    -0.06               -0.02   
max                -0.02               -0.03    -0.06               -0.02   

       Airport Lounge  Airport Service      ...        Wine Bar  Wine Shop  \
count            6.00     6.000000e+00      ...            6.00       6.00   
mean            -0.04    -5.000000e-02      ...           -0.08      -0.06   
std              0.00     7.601177e-18      ...            0.00       0.00   
min             -0.04    -5.000000e-02      ...           -0.08      -0.06   
25%             -0.04    -5.000000e-02      ...           -0.08      -0.06   
50%             -0.04    -5.000000e-02      ...           -0.08      -0.06   
75%             -0.04    -5.000000e-02      ...           -0.08      -0.06   
max             -0.04    -5.000000e-02      ...           -0.08      -0.06   

       Winery  Wings Joint  Women's Store  Xinjiang Restaurant  Yoga Studio  \
count    6.00         6.00           6.00                 6.00         6.00   
mean    -0.03        -0.08          -0.06                -0.02        -0.07   
std      0.00         0.00           0.00                 0.00         0.00   
min     -0.03        -0.08          -0.06                -0.02        -0.07   
25%     -0.03        -0.08          -0.06                -0.02        -0.07   
50%     -0.03        -0.08          -0.06                -0.02        -0.07   
75%     -0.03        -0.08          -0.06                -0.02        -0.07   
max     -0.03        -0.08          -0.06                -0.02        -0.07   

        Zoo  Zoo Exhibit  Cluster Label  
count  6.00         6.00            6.0  
mean  -0.04        -0.04            1.0  
std    0.00         0.00            0.0  
min   -0.04        -0.04            1.0  
25%   -0.04        -0.04            1.0  
50%   -0.04        -0.04            1.0  
75%   -0.04        -0.04            1.0  
max   -0.04        -0.04            1.0  

[8 rows x 596 columns]

In [23]:
merged[merged["Cluster Label"] == 2].round(2).describe()

ATM  Accessories Store  Adult Boutique  Advertising Agency  \
count  1.00               1.00            1.00                1.00   
mean  -0.08              -0.04           -0.02               -0.02   
std     NaN                NaN             NaN                 NaN   
min   -0.08              -0.04           -0.02               -0.02   
25%   -0.08              -0.04           -0.02               -0.02   
50%   -0.08              -0.04           -0.02               -0.02   
75%   -0.08              -0.04           -0.02               -0.02   
max   -0.08              -0.04           -0.02               -0.02   

       Afghan Restaurant  African Restaurant  Airport  Airport Food Court  \
count               1.00                1.00     1.00                1.00   
mean               -0.02               -0.03    -0.06               -0.02   
std                  NaN                 NaN      NaN                 NaN   
min                -0.02               -0.03    -0.06               -0.02   
25%                -0.02               -0.03    -0.06               -0.02   
50%                -0.02               -0.03    -0.06               -0.02   
75%                -0.02               -0.03    -0.06               -0.02   
max                -0.02               -0.03    -0.06               -0.02   

       Airport Lounge  Airport Service      ...        Wine Bar  Wine Shop  \
count            1.00             1.00      ...            1.00       1.00   
mean            -0.04            -0.05      ...           -0.08      -0.06   
std               NaN              NaN      ...             NaN        NaN   
min             -0.04            -0.05      ...           -0.08      -0.06   
25%             -0.04            -0.05      ...           -0.08      -0.06   
50%             -0.04            -0.05      ...           -0.08      -0.06   
75%             -0.04            -0.05      ...           -0.08      -0.06   
max             -0.04            -0.05      ...           -0.08      -0.06   

       Winery  Wings Joint  Women's Store  Xinjiang Restaurant  Yoga Studio  \
count    1.00         1.00           1.00                 1.00         1.00   
mean    -0.03        -0.08          -0.06                -0.02        -0.07   
std       NaN          NaN            NaN                  NaN          NaN   
min     -0.03        -0.08          -0.06                -0.02        -0.07   
25%     -0.03        -0.08          -0.06                -0.02        -0.07   
50%     -0.03        -0.08          -0.06                -0.02        -0.07   
75%     -0.03        -0.08          -0.06                -0.02        -0.07   
max     -0.03        -0.08          -0.06                -0.02        -0.07   

        Zoo  Zoo Exhibit  Cluster Label  
count  1.00         1.00            1.0  
mean  -0.04        -0.04            2.0  
std     NaN          NaN            NaN  
min   -0.04        -0.04            2.0  
25%   -0.04        -0.04            2.0  
50%   -0.04        -0.04            2.0  
75%   -0.04        -0.04            2.0  
max   -0.04        -0.04            2.0  

[8 rows x 596 columns]

In [24]:
merged[merged["Cluster Label"] == 3].round(2).describe()

ATM  Accessories Store  Adult Boutique  Advertising Agency  \
count  9.700000e+01       9.700000e+01    9.700000e+01        9.700000e+01   
mean  -8.000000e-02      -4.000000e-02   -2.000000e-02       -2.000000e-02   
std    5.579952e-17       2.789976e-17    1.394988e-17        1.394988e-17   
min   -8.000000e-02      -4.000000e-02   -2.000000e-02       -2.000000e-02   
25%   -8.000000e-02      -4.000000e-02   -2.000000e-02       -2.000000e-02   
50%   -8.000000e-02      -4.000000e-02   -2.000000e-02       -2.000000e-02   
75%   -8.000000e-02      -4.000000e-02   -2.000000e-02       -2.000000e-02   
max   -8.000000e-02      -4.000000e-02   -2.000000e-02       -2.000000e-02   

       Afghan Restaurant  African Restaurant       Airport  \
count       9.700000e+01           97.000000  9.700000e+01   
mean       -2.000000e-02            1.070928 -6.000000e-02   
std         1.394988e-17            7.144269  8.369928e-17   
min        -2.000000e-02           -0.030000 -6.000000e-02   
25%        -2.000000e-02           -0.030000 -6.000000e-02   
50%        -2.000000e-02           -0.030000 -6.000000e-02   
75%        -2.000000e-02           -0.030000 -6.000000e-02   
max        -2.000000e-02           64.040000 -6.000000e-02   

       Airport Food Court  Airport Lounge  Airport Service      ...        \
count        9.700000e+01    9.700000e+01     9.700000e+01      ...         
mean        -2.000000e-02   -4.000000e-02    -5.000000e-02      ...         
std          1.394988e-17    2.789976e-17     9.764916e-17      ...         
min         -2.000000e-02   -4.000000e-02    -5.000000e-02      ...         
25%         -2.000000e-02   -4.000000e-02    -5.000000e-02      ...         
50%         -2.000000e-02   -4.000000e-02    -5.000000e-02      ...         
75%         -2.000000e-02   -4.000000e-02    -5.000000e-02      ...         
max         -2.000000e-02   -4.000000e-02    -5.000000e-02      ...         

        Wine Bar     Wine Shop        Winery  Wings Joint  Women's Store  \
count  97.000000  9.700000e+01  9.700000e+01    97.000000   9.700000e+01   
mean    0.132165 -6.000000e-02 -3.000000e-02    -0.025567  -6.000000e-02   
std     1.550980  8.369928e-17  4.184964e-17     0.536103   8.369928e-17   
min    -0.080000 -6.000000e-02 -3.000000e-02    -0.080000  -6.000000e-02   
25%    -0.080000 -6.000000e-02 -3.000000e-02    -0.080000  -6.000000e-02   
50%    -0.080000 -6.000000e-02 -3.000000e-02    -0.080000  -6.000000e-02   
75%    -0.080000 -6.000000e-02 -3.000000e-02    -0.080000  -6.000000e-02   
max    13.640000 -6.000000e-02 -3.000000e-02     5.200000  -6.000000e-02   

       Xinjiang Restaurant  Yoga Studio           Zoo   Zoo Exhibit  \
count         9.700000e+01    97.000000  9.700000e+01  9.700000e+01   
mean         -2.000000e-02     0.065258 -4.000000e-02 -4.000000e-02   
std           1.394988e-17     0.768483  2.789976e-17  2.789976e-17   
min          -2.000000e-02    -0.070000 -4.000000e-02 -4.000000e-02   
25%          -2.000000e-02    -0.070000 -4.000000e-02 -4.000000e-02   
50%          -2.000000e-02    -0.070000 -4.000000e-02 -4.000000e-02   
75%          -2.000000e-02    -0.070000 -4.000000e-02 -4.000000e-02   
max          -2.000000e-02     5.080000 -4.000000e-02 -4.000000e-02   

       Cluster Label  
count           97.0  
mean             3.0  
std              0.0  
min              3.0  
25%              3.0  
50%              3.0  
75%              3.0  
max              3.0  

[8 rows x 596 columns]

In [25]:
merged[merged["Cluster Label"] == 4].round(2).describe()

ATM  Accessories Store  Adult Boutique  Advertising Agency  \
count  3218.000000        3218.000000    3.218000e+03         3218.000000   
mean     -0.076774           0.001687   -2.000000e-02            0.007014   
std       0.098627           1.227165    1.346355e-15            1.263519   
min      -0.080000          -0.040000   -2.000000e-02           -0.020000   
25%      -0.080000          -0.040000   -2.000000e-02           -0.020000   
50%      -0.080000          -0.040000   -2.000000e-02           -0.020000   
75%      -0.080000          -0.040000   -2.000000e-02           -0.020000   
max       4.090000          45.820000   -2.000000e-02           69.520000   

       Afghan Restaurant  African Restaurant      Airport  Airport Food Court  \
count       3.218000e+03        3.218000e+03  3218.000000         3218.000000   
mean       -2.000000e-02       -3.000000e-02     0.013527           -0.009276   
std         1.346355e-15        8.987264e-16     1.162303            0.608348   
min        -2.000000e-02       -3.000000e-02    -0.060000           -0.020000   
25%        -2.000000e-02       -3.000000e-02    -0.060000           -0.020000   
50%        -2.000000e-02       -3.000000e-02    -0.060000           -0.020000   
75%        -2.000000e-02       -3.000000e-02    -0.060000           -0.020000   
max        -2.000000e-02       -3.000000e-02    45.170000           34.490000   

       Airport Lounge  Airport Service      ...           Wine Bar  \
count     3218.000000      3218.000000      ...        3218.000000   
mean        -0.026672         0.011075      ...           0.006958   
std          0.555114         1.233329      ...           1.204839   
min         -0.040000        -0.050000      ...          -0.080000   
25%         -0.040000        -0.050000      ...          -0.080000   
50%         -0.040000        -0.050000      ...          -0.080000   
75%         -0.040000        -0.050000      ...          -0.080000   
max         27.410000        34.950000      ...          27.370000   

         Wine Shop       Winery  Wings Joint  Women's Store  \
count  3218.000000  3218.000000  3218.000000    3218.000000   
mean     -0.012219     0.015270    -0.053151      -0.056855   
std       1.198984     1.240258     0.567478       0.093647   
min      -0.060000    -0.030000    -0.080000      -0.060000   
25%      -0.060000    -0.030000    -0.080000      -0.060000   
50%      -0.060000    -0.030000    -0.080000      -0.060000   
75%      -0.060000    -0.030000    -0.080000      -0.060000   
max      53.920000    48.640000    15.750000       3.380000   

       Xinjiang Restaurant  Yoga Studio          Zoo  Zoo Exhibit  \
count         3.218000e+03  3218.000000  3218.000000  3218.000000   
mean         -2.000000e-02     0.009372     0.014117     0.026619   
std           1.346355e-15     1.213524     1.232391     1.262981   
min          -2.000000e-02    -0.070000    -0.040000    -0.040000   
25%          -2.000000e-02    -0.070000    -0.040000    -0.040000   
50%          -2.000000e-02    -0.070000    -0.040000    -0.040000   
75%          -2.000000e-02    -0.070000    -0.040000    -0.040000   
max          -2.000000e-02    25.680000    39.560000    35.920000   

       Cluster Label  
count         3218.0  
mean             4.0  
std              0.0  
min              4.0  
25%              4.0  
50%              4.0  
75%              4.0  
max              4.0  

[8 rows x 596 columns]

In [26]:
sizemap = neighborhoods.reset_index()
sizemap['Neighborhood'] = sizemap['Name']
sizemap['Neighborhood Latitude'] = sizemap['Location'].apply(lambda x: x[0]).round(5).astype(str)
sizemap['Neighborhood Longitude'] = sizemap['Location'].apply(lambda x: x[1]).round(3).astype(str)
sizemap.set_index(["Neighborhood", "Neighborhood Latitude", "Neighborhood Longitude"], inplace=True)
sizemap.loc['33rd St. Industrial']

index                 Name  \
Neighborhood Latitude Neighborhood Longitude                               
28.50493              -81.436                 12060  33rd St. Industrial   

                                                                              Location  \
Neighborhood Latitude Neighborhood Longitude                                             
28.50493              -81.436                 (28.504929203699444, -81.43557640697989)   

                                                   Size  
Neighborhood Latitude Neighborhood Longitude             
28.50493              -81.436                 20.376481

In [27]:
names = merged.index.get_level_values('Neighborhood').to_series()
lats = merged.index.get_level_values('Neighborhood Latitude').to_series().round(5).astype(str)
lngs = merged.index.get_level_values('Neighborhood Longitude').to_series().round(3).astype(str)
merged["Size"] = [sizemap.loc[a].Size[0] for a in list(zip(names, lats, lngs))]
merged.head(15)

/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:4: PerformanceWarning: indexing past lexsort depth may impact performance.
  after removing the cwd from sys.path.


ATM  \
Neighborhood        Neighborhood Latitude Neighborhood Longitude             
19th Ward           43.143592             -77.648521             -0.078638   
29 North            38.062210             -78.487690             -0.078638   
33rd St. Industrial 28.504929             -81.435576             -0.078638   
39th East           39.044526             -94.375892             -0.078638   
65th St. West       34.679176             -92.377483             -0.078638   
9th Ward Area       39.760470             -75.536849             -0.078638   
ACCENT              41.604207             -93.558783             -0.078638   
ASU-College Hills   31.437276             -100.469859            -0.078638   
Abbott Loop         61.148353             -149.816400            -0.078638   
Abbott McKinley     42.850643             -78.817091             -0.078638   
Aberdeen            37.022693             -76.404651             -0.078638   
Abilene Heights     32.467123             -99.698630             -0.078638   
Aboite Meadows      41.048878             -85.267200             -0.078638   
Acorn               30.070826             -94.195259             -0.078638   
Acre                42.643045             -71.325620             -0.078638   

                                                                  Accessories Store  \
Neighborhood        Neighborhood Latitude Neighborhood Longitude                      
19th Ward           43.143592             -77.648521                      -0.042641   
29 North            38.062210             -78.487690                      -0.042641   
33rd St. Industrial 28.504929             -81.435576                      -0.042641   
39th East           39.044526             -94.375892                      -0.042641   
65th St. West       34.679176             -92.377483                      -0.042641   
9th Ward Area       39.760470             -75.536849                      -0.042641   
ACCENT              41.604207             -93.558783                      -0.042641   
ASU-College Hills   31.437276             -100.469859                     -0.042641   
Abbott Loop         61.148353             -149.816400                     -0.042641   
Abbott McKinley     42.850643             -78.817091                      -0.042641   
Aberdeen            37.022693             -76.404651                      -0.042641   
Abilene Heights     32.467123             -99.698630                      -0.042641   
Aboite Meadows      41.048878             -85.267200                      -0.042641   
Acorn               30.070826             -94.195259                      -0.042641   
Acre                42.643045             -71.325620                      -0.042641   

                                                                  Adult Boutique  \
Neighborhood        Neighborhood Latitude Neighborhood Longitude                   
19th Ward           43.143592             -77.648521                   -0.023981   
29 North            38.062210             -78.487690                   -0.023981   
33rd St. Industrial 28.504929             -81.435576                   -0.023981   
39th East           39.044526             -94.375892                   -0.023981   
65th St. West       34.679176             -92.377483                   -0.023981   
9th Ward Area       39.760470             -75.536849                   -0.023981   
ACCENT              41.604207             -93.558783                   -0.023981   
ASU-College Hills   31.437276             -100.469859                  -0.023981   
Abbott Loop         61.148353             -149.816400                  -0.023981   
Abbott McKinley     42.850643             -78.817091                   -0.023981   
Aberdeen            37.022693             -76.404651                   -0.023981   
Abilene Heights     32.467123             -99.698630                   -0.023981   
Aboite Meadows      41.048878             -85.267200                   -0.023981   
Acor

In [29]:
import numpy as np
import matplotlib.cm as cm
import matplotlib.colors as colors

# create map
map_clusters = folium.Map(
    location=[36.64699473120942, -75.99394080442949],
    zoom_start=4.3
)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i+x+(i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, hood, cluster, size in zip(
    merged.index.get_level_values('Neighborhood Latitude'), 
    merged.index.get_level_values('Neighborhood Longitude'), 
    merged.index.get_level_values('Neighborhood'), 
    merged['Cluster Label'],
    merged['Size']
):
    label = folium.Popup(str(hood) + ' Cluster ' + str(cluster), parse_html=True)
    folium.Circle(
        [lat, lon],
        radius=250 * math.sqrt(size/math.pi),
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_clusters)

map_clusters.save("cluster_map.html")
map_clusters